In [1]:
import bs4
import requests
import pandas as pd
import os
import time
from IPython.display import clear_output

In [2]:
# 소스 요청 함수
def getSource(site):
    header_info = {
        'User-Agent' : 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/135.0.0.0 Safari/537.36'
    }

    # 요청한다.
    response = requests.get(site, headers=header_info)
    # bs4 객체를 생성한다.
    ## BeautifulSoup은 HTML 또는 XML 문서를 파싱하고 구조화해서 데이터를 쉽게 추출할 수 있도록 도와주는 도구
    soup = bs4.BeautifulSoup(response.text, 'lxml')
    return soup

In [3]:
def getData(soup, file_name):
    a1 = soup.select_one('#mArticle')
    if not a1:
        return

    divs = a1.select('div')

    data_list = []

    for div in divs:
        # 제목
        title = div.select_one('a.link_post > strong')

        # 카테고리
        # #mArticle > div:nth-child(3) > div > a
        category = div.select_one('a.link_cate')
        
        # 작성 날짜
        date = div.select_one('span.txt_date')

        # 모든 요소가 존재할 때만 저장
        if title and category and date:
            data_list.append({
                '제목': title.text.strip(),
                '카테고리': category.text.strip(),
                '작성날짜': date.text.strip()
            })

    # 데이터프레임 생성 및 저장
    if data_list:
        df1 = pd.DataFrame(data_list)
        if not os.path.exists(file_name):
            df1.to_csv(file_name, encoding='utf-8-sig', index=False)
        else:
            df1.to_csv(file_name, encoding='utf-8-sig', index=False, header=False, mode='a')


In [4]:
# 3. 다음 페이지 주소를 가져오는 함수
def getNextPage(soup):
    next_tag = soup.select_one('#mArticle > div.area_paging > span > a.btn_next')
    if next_tag:
        href = next_tag.get('href')
        return href if href else None
    return None


In [5]:
# 4. 수집 실행 로직
site = 'https://tobepotato.tistory.com/'
page = ''

while True:
    time.sleep(1)
    clear_output(wait=True)
    print(f'{site}{page} 수집중...')

    soup = getSource(site + page)
    getData(soup, 'tistoryData.csv')

    page = getNextPage(soup)
    if page is None:
        print('수집완료')
        break

https://tobepotato.tistory.com//?page=3 수집중...
수집완료
